# Constants from DB to HDF5 #

Version 0.1, Author: S. Hauf

Currently available instances are LPD1M1 and AGIPD1M1

In [ ]:
detector_instance = "LPD1M1"  # the detector instance to get constants for e.g. LPD1M1, required
out_file = "/gpfs/exfel/data/scratch/haufs/test/test.h5"  # HDF5 file to output constants into, required
valid_at = ""  # ISO formatted date for which constants shoudl be valid. Leave empty to get most current ones
cal_db_interface = "tcp://max-exfl015:5005"
modules = [-1]  # modules to get data from, in terms of numerical quadrant indices, range allowed

In [ ]:
dtype = "LPD" if "LPD" in detector_instance.upper() else "AGIPD"
darkconst = ["Offset", "Noise", "SlopesPC", "SlopesCI", "BadPixelsDark", "BadPixelsPC", "BadPixelsCI"]
skip = ["BadPixels"]

overwrites = {"LPD": {"SlopesFF": {"memory_cells": 1},
                      "BadPixelsFF": {"memory_cells": 1}}}

if modules[0] == -1:
    modules = list(range(16))

In [ ]:
import copy
import datetime
import inspect

import h5py
from iCalibrationDB import Conditions, ConstantMetaData, Constants, Detectors, Versions


def extend_parms(detector_instance):
    import inspect

    from iCalibrationDB import Conditions
    existing = set()
    def extract_parms(cls):
        args, varargs, varkw, defaults = inspect.getargspec(cls.__init__)
        pList = []        
        for i, arg in enumerate(args[1:][::-1]):
            if arg in existing:
                continue
            
            existing.add(arg)
            
            if i < len(defaults):
                default = defaults[::-1][i]                
                if str(default).isdigit():
                    pList.append("{} = {}".format(arg, default))
                elif default is None or default == "None":
                    pList.append("{} = \"None\"".format(arg))
                else:
                    pList.append("{} = \"{}\"".format(arg, default))
            else:
                pList.append("{} = 0.  # required".format(arg))
        return set(pList[::-1])  # mandatories first
    dtype = "LPD" if "LPD" in detector_instance.upper() else "AGIPD"
    all_conditions = set()
    for c in dir(Conditions):
        if c[:2] != "__":
            condition = getattr(Conditions, c)
            parms = extract_parms(getattr(condition, dtype))
            [all_conditions.add(p) for p in parms]
    return "\n".join(all_conditions)

In [ ]:
det = getattr(Detectors, detector_instance)

In [ ]:
ip = get_ipython()

In [ ]:
first_cell = next(ip.history_manager.get_range(ip.history_manager.get_last_session_id(), 1, 2, raw=True))

In [ ]:
_, _, code = first_cell
code = code.split("\n")
parms = {}
for c in code:
    n, v = c.split("=")
    n = n.strip()
    v = v.strip()
    try:
        parms[n] = float(v)
    except:
        parms[n] = str(v) if not isinstance(v, str) else v
    if parms[n] == "None" or parms[n] == "'None'":
        parms[n] = None

In [ ]:
ofile = h5py.File(out_file, "w")

detector = getattr(Detectors, detector_instance)
for i in modules:
    qm = "Q{}M{}".format(i//4+1, i%4+1)
    module = getattr(detector, qm)
    dconstants = getattr(Constants, dtype)
    for const in dir(dconstants):
        if const[:2] != "__":
            
            if const in skip:
                continue
            
            cparms = copy.copy(parms)
            if dtype in overwrites:
                do = overwrites[dtype]
                if const in do:
                    for arg, v in do[const].items():
                        cparms[arg] = v
            
            try:
                metadata = ConstantMetaData()
                cons = getattr(dconstants, const)()
                metadata.calibration_constant = cons

                # set the operating condition

                cond =  Conditions.Dark if const in darkconst else Conditions.Illuminated

                condition = getattr(cond, dtype)

                args, varargs, varkw, defaults = inspect.getargspec(condition.__init__)
                alist = []
                plist = {}
                for i, arg in enumerate(args[1:][::-1]):
                    #if i < len(defaults):
                    #    plist[arg] = parms[arg]
                    #else:
                    #    alist.append(parms[arg])
                    plist[arg] = cparms[arg]


                condition = condition(**plist)

                metadata.detector_condition = condition

                # specify the a version for this constant
                if valid_at is None or valid_at == "":
                    creation_time = datetime.datetime.now()
                    metadata.calibration_constant_version = Versions.Now(
                        device=module)
                else:
                    metadata.calibration_constant_version = Versions.Timespan(
                        device=module,
                        start=valid_at)
                    creation_time = valid_at

                ctime = creation_time.isoformat() if not isinstance(creation_time, str) else creation_time

                metadata.retrieve(cal_db_interface, when=ctime)
                
                ofile["{}/{}/data".format(qm, const)] = metadata.calibration_constant.data
            except Exception as e:
                print("Failed for const {} of {}: {}".format(const, qm, e))
ofile.close()         